In [1]:
import pandas as pd
import numpy as np
import spacy
from spacy import displacy
import networkx as nx

In [2]:
!python3 -m spacy download en_core_web_sm

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 6.6 MB/s eta 0:00:0000:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [3]:
# Load spacy English languague model
NER = spacy.load("en_core_web_sm")

text = open('./data/burial-rites.txt').read()
doc = NER(text)

Load character names

In [22]:
character_df = pd.read_csv("characters.csv")

Find and filter all entities in book for characters only

In [23]:
sent_entity_df = []

# Loop through sentences, store named entity list for each sentence
for sent in doc.sents:
    entity_list = [ent.text for ent in sent.ents]
    sent_entity_df.append({"sentence": sent, "entities": entity_list})
    
sent_entity_df = pd.DataFrame(sent_entity_df)

In [6]:
sent_entity_df # Entities in every sentence

sentence   
0                         (
, About, Burial, Rites, \n)  \
1     (In, northern, Iceland, ,, 1829, ,, Agnes, Mag...   
2     (Agnes, is, sent, to, wait, out, the, time, le...   
3     (Horrified, to, have, a, \n, convicted, murder...   
4     (Only, \n, Tóti, ,, the, young, assistant, rev...   
5     (As, the, \n, summer, months, fall, away, to, ...   
6     (And, as, the, days, to, her, execution, draw,...   
7     (In, beautiful, ,, cut, -, glass, prose, ,, \n...   
8     (‘, Burial, Rites, is, an, accomplished, gem, ...   
9     (GERALDINE, BROOKS, \n, ‘, So, gripping, I, wa...   
10    (Hannah, Kent, ’s, debut, novel, is, outstandi...   
11    (MADELINE, MILLER, ,, Orange, Prize, -, winnin...   
12    (Agnes, \n, Magnúsdóttir, is, therefore, liter...   
13    (Because, of, this, system, ,, blood, members,...   
14        (A, NOTE, ON, ICELANDIC, PRONUNCIATION, \n\n)   
15    (For, ease, of, pronunciation, ,, not, all, Ic...   
16    (The, consonants, ð, (, Ð, ), and, þ, (, Þ, ),...   
17    (The, pronunciation, of, certain, vowels, are,...   
18                           (I, LOVED, BEST, ., ’, \n)   
19               (Laxdæla, Saga, \n\n
, PROLOGUE, \n\n)   
20                        (THEY, SAID, I, MUST, DIE, .)   
21    (They, said, that, I, stole, the, breath, from...   
22    (I, imagine, ,, then, ,, that, we, are, all, c...   
23    (I, will, vanish, into, the, \n, air, and, the...   
24    (They, will, blow, us, all, out, ,, one, by, o...   
25                    (Where, will, I, be, then, ?, \n)   
26    (Sometimes, I, think, I, see, it, again, ,, th...   
27    (Sometimes, I, \n, can, feel, the, ache, of, w...   
28    (There, was, a, moment, \n, during, that, nigh...   
29    (I, looked, back, to, watch, the, fire, ,, and...   
30                                  (The, smoke, ., \n)   
31              (It, was, n’t, always, so, cold, ., \n)   
32                       (I, hear, footsteps, ., \n\n
)   
33    (CHAPTER, ONE, \n\n, Public, Notice, \n, THERE...   
34    (There, is, one, cow, ,, a, few, horses, ,, a,...   
35    (All, this, will, be, \n, sold, if, a, decent,...   
36    (All, valuables, will, be, awarded, to, the, \...   
37    (If, the, auction, is, not, possible, due, to,...   
38    (DISTRICT, COMMISSIONER, \n\n, Björn, Blöndal,...   
39    (To, the, Very, Reverend, Jóhann, Tómasson, ,,...   
40    (As, my, \n, Reverend, is, aware, ,, there, wa...   
41    (His, conviction, and, punishment, for, \n, ro...   
42    (However, ,, we, have, not, had, any, letters,...   
43    (The, Land, Court, judge, convicted, Pétur, on...   
44    (Therefore, ,, in, answer, to, your, enquiry, ...   
45    (These, people, are, expressly, defined, in, t...   
46    (DISTRICT, COMMISSIONER, \n\n, Björn, Blöndal,...   
47    (Firstly, ,, I, wish, to, extend, to, you, my,...   
48    (Your, \n, parishioners, say, that, you, are, ...   
49    (It, is, of, considerable, joy, to, me, to, kn...   
50    (Secondly, ,, I, ,, in, my, capacity, as, Dist...   
51    (As, you, will, be, aware, ,, our, community, ...   
52    (The, Illugastadir, murders, ,, committed, las...   
53    (As, District, Commissioner, for, Húnavatn, ,,...   
54    (It, is, with, this, event, in, mind, that, I,...   
55    (As, you, will, recall, ,, I, related, the, ev...   
56    (Allow, me, to, repeat, what, occurred, ,, thi...   
57    (Last, year, ,, on, the, night, between, the, ...   
58    (Pétur, and, Natan, \n, were, found, in, the, ...   
59    (This, discovery, led, to, an, enquiry, ,, and...   
60    (On, \n, the, 2nd, of, July, last, year, the, ...   
61    (The, death, sentences, were, upheld, \n, in, ...   
62    (The, case, is, currently, being, tried, in, C...   
63    (The, \n, name, of, the, convicted, man, is, F...   
64    (The, women, are, workmaids, ,, named, Sigrídu...   
65    (These, convicted, persons, are, currently, he...   
66    (Fridrik, Sigurdsson, has, been, \n, taken, in...   
67    (Agnes, Magnúsdóttir, was, to

In [7]:
# Function to filter out non-character entities
def filter_entity(ent_list, character_df):
    return [ent for ent in ent_list 
            if ent in list(character_df.alias) 
            or ent in list(character_df.character_firstname)]

In [21]:
sent_entity_df['character_entities'] = sent_entity_df['entities'].apply(lambda x: filter_entity(x, character_df))

# Filter out sentences that don't have any character entities
sent_entity_df_filtered = sent_entity_df[sent_entity_df['character_entities'].map(len) > 0]

In [9]:
# Take only first name of characters
sent_entity_df_filtered['character_entities'] = sent_entity_df_filtered['character_entities'].apply(lambda x: [item.split()[0] 
                                                                                                               for item in x])

/tmp/ipykernel_1327/364234938.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sent_entity_df_filtered['character_entities'] = sent_entity_df_filtered['character_entities'].apply(lambda x: [item.split()[0]


In [10]:
pd.reset_option('^display.', silent=True)
sent_entity_df_filtered

sentence   
2     (Agnes, is, sent, to, wait, out, the, time, le...  \
3     (Horrified, to, have, a, \n, convicted, murder...   
4     (Only, \n, Tóti, ,, the, young, assistant, rev...   
5     (As, the, \n, summer, months, fall, away, to, ...   
43    (The, Land, Court, judge, convicted, Pétur, on...   
...                                                 ...   
8504  (All, place, names, used, in, this, novel, are...   
8505  (Many, known, and, established, facts, about, ...   
8506  (The, \n, family, at, the, farm, of, Kornsá, d...   
8507  (The, nature, of, their, relationship, ,, incl...   
8513  (While, wonderfully, useful, ,, some, of, thes...   

                                               entities character_entities  
2                             [Agnes, Jón Jónsson, two]            [Agnes]  
3                                               [Agnes]            [Agnes]  
4                                         [Tóti, Agnes]      [Tóti, Agnes]  
5              [the\nsummer months fall, winter, Agnes]            [Agnes]  
43    [Land Court, Pétur, 5th, February last year, f...            [Pétur]  
...                                                 ...                ...  
8504                                  [Agnes, this day]            [Agnes]  
8505                                            [Agnes]            [Agnes]  
8506  [Kornsá, Agnes, Stóra-Borg, Agnes, Þórvarður J...     [Agnes, Agnes]  
8507                                     [first, Agnes]            [Agnes]  
8513                                            [Agnes]            [Agnes]  

[2479 rows x 3 columns]

Create relationships

In [11]:
window_size = 5
relationships = []

for i in range(sent_entity_df_filtered.index[-1]):
    end_i = min(i+5, sent_entity_df_filtered.index[-1])
    char_list = sum((sent_entity_df_filtered.loc[i: end_i].character_entities), [])
    
    # Remove duplicated characters that are next to each other
    char_unique = [char_list[i] for i in range(len(char_list)) 
                   if (i==0) or char_list[i] != char_list[i-1]]
    
    if len(char_unique) > 1:
        for idx, a in enumerate(char_unique[:-1]):
            b = char_unique[idx + 1]
            relationships.append({"source": a, "target": b})

In [12]:
relationship_df = pd.DataFrame(relationships)

In [13]:
pd.set_option('display.max_rows', None)
relationship_df

source      target
0          Agnes        Tóti
1           Tóti       Agnes
2          Agnes        Tóti
3           Tóti       Agnes
4          Agnes        Tóti
5           Tóti       Agnes
6          Agnes        Tóti
7           Tóti       Agnes
8           Tóti       Agnes
9          Pétur       Natan
10         Pétur       Natan
11         Pétur       Natan
12         Pétur       Natan
13         Pétur       Natan
14         Pétur       Natan
15         Pétur       Natan
16         Pétur       Natan
17         Pétur       Natan
18         Pétur       Natan
19         Pétur       Natan
20          Tóti         Jón
21           Jón        Tóti
22           Jón        Tóti
23           Jón        Tóti
24           Jón        Tóti
25           Jón        Tóti
26           Jón        Tóti
27        Steina     Margrét
28       Margrét         Jón
29       Margrét         Jón
30       Margrét         Jón
31       Margrét         Jón
32           Jón      Steina
33       Margrét         Jón
34           Jón      Steina
35       Margrét         Jón
36           Jón      Steina
37        Steina       Lauga
38        Steina       Lauga
39         Lauga      Steina
40         Lauga      Steina
41         Lauga      Steina
42         Lauga      Steina
43         Lauga      Steina
44        Steina       Lauga
45        Steina       Lauga
46        Steina       Lauga
47         Lauga      Steina
48         Lauga      Steina
49         Lauga      Steina
50         Lauga      Steina
51        Steina       Lauga
52        Steina       Lauga
53         Lauga      Steina
54         Lauga      Steina
55         Lauga      Steina
56        Steina       Lauga
57         Lauga      Steina
58        Steina       Lauga
59         Lauga      Steina
60         Lauga      Steina
61        Steina       Lauga
62         Lauga      Steina
63        Steina       Lauga
64         Lauga      Steina
65         Lauga      Steina
66         Lauga      Steina
67        Steina       Lauga
68        Steina       Lauga
69        Steina       Lauga
70         Lauga      Steina
71         Lauga      Steina
72         Lauga      Steina
73        Steina       Lauga
74         Lauga     Kristín
75         Lauga      Steina
76        Steina       Lauga
77         Lauga     Kristín
78       Kristín       Lauga
79        Steina       Lauga
80         Lauga     Kristín
81       Kristín       Lauga
82        Steina       Lauga
83         Lauga     Kristín
84       Kristín       Lauga
85         Lauga     Kristín
86       Kristín       Lauga
87         Lauga     Kristín
88       Kristín       Lauga
89         Lauga      Steina
90         Lauga      Steina
91         Lauga      Steina
92        Steina       Lauga
93        Steina       Lauga
94        Steina       Lauga
95        Steina       Lauga
96         Lauga      Steina
97        Steina     Kristín
98         Lauga      Steina
99        Steina     Kristín
100      Kristín      Steina
101        Lauga      Steina
102       Steina     Kristín
103      Kristín      Steina
104       Steina     Kristín
105      Kristín      Steina
106       Steina     Kristín
107      Kristín      Steina
108       Steina     Kristín
109      Kristín      Steina
110       Steina       Lauga
111        Lauga     Kristín
112        Lauga     Kristín
113        Lauga     Kristín
114        Lauga     Kristín
115      Kristín      Steina
116        Lauga     Kristín
117      Kristín      Steina
118        Lauga     Kristín
119      Kristín      Steina
120       Steina     Kristín
121       Steina     Kristín
122      Kristín       Lauga
123        Lauga      Steina
124      Kristín       Lauga
125        Lauga      Steina
126      Kristín       Lauga
127        Lauga      Steina
128      Kristín       Lauga
129        Lauga      Steina
130        Lauga      Steina
131        Lauga      Steina
132        Lauga      Steina
133        Lauga      Steina
134        Lauga      Steina
135        Lauga      Steina
136        Lauga      Steina
137     

In [14]:
# Sort the cases with a->b and b->a
relationship_df = pd.DataFrame(np.sort(relationship_df.values, axis = 1), columns = relationship_df.columns)
relationship_df

source      target
0          Agnes        Tóti
1          Agnes        Tóti
2          Agnes        Tóti
3          Agnes        Tóti
4          Agnes        Tóti
5          Agnes        Tóti
6          Agnes        Tóti
7          Agnes        Tóti
8          Agnes        Tóti
9          Natan       Pétur
10         Natan       Pétur
11         Natan       Pétur
12         Natan       Pétur
13         Natan       Pétur
14         Natan       Pétur
15         Natan       Pétur
16         Natan       Pétur
17         Natan       Pétur
18         Natan       Pétur
19         Natan       Pétur
20           Jón        Tóti
21           Jón        Tóti
22           Jón        Tóti
23           Jón        Tóti
24           Jón        Tóti
25           Jón        Tóti
26           Jón        Tóti
27       Margrét      Steina
28           Jón     Margrét
29           Jón     Margrét
30           Jón     Margrét
31           Jón     Margrét
32           Jón      Steina
33           Jón     Margrét
34           Jón      Steina
35           Jón     Margrét
36           Jón      Steina
37         Lauga      Steina
38         Lauga      Steina
39         Lauga      Steina
40         Lauga      Steina
41         Lauga      Steina
42         Lauga      Steina
43         Lauga      Steina
44         Lauga      Steina
45         Lauga      Steina
46         Lauga      Steina
47         Lauga      Steina
48         Lauga      Steina
49         Lauga      Steina
50         Lauga      Steina
51         Lauga      Steina
52         Lauga      Steina
53         Lauga      Steina
54         Lauga      Steina
55         Lauga      Steina
56         Lauga      Steina
57         Lauga      Steina
58         Lauga      Steina
59         Lauga      Steina
60         Lauga      Steina
61         Lauga      Steina
62         Lauga      Steina
63         Lauga      Steina
64         Lauga      Steina
65         Lauga      Steina
66         Lauga      Steina
67         Lauga      Steina
68         Lauga      Steina
69         Lauga      Steina
70         Lauga      Steina
71         Lauga      Steina
72         Lauga      Steina
73         Lauga      Steina
74       Kristín       Lauga
75         Lauga      Steina
76         Lauga      Steina
77       Kristín       Lauga
78       Kristín       Lauga
79         Lauga      Steina
80       Kristín       Lauga
81       Kristín       Lauga
82         Lauga      Steina
83       Kristín       Lauga
84       Kristín       Lauga
85       Kristín       Lauga
86       Kristín       Lauga
87       Kristín       Lauga
88       Kristín       Lauga
89         Lauga      Steina
90         Lauga      Steina
91         Lauga      Steina
92         Lauga      Steina
93         Lauga      Steina
94         Lauga      Steina
95         Lauga      Steina
96         Lauga      Steina
97       Kristín      Steina
98         Lauga      Steina
99       Kristín      Steina
100      Kristín      Steina
101        Lauga      Steina
102      Kristín      Steina
103      Kristín      Steina
104      Kristín      Steina
105      Kristín      Steina
106      Kristín      Steina
107      Kristín      Steina
108      Kristín      Steina
109      Kristín      Steina
110        Lauga      Steina
111      Kristín       Lauga
112      Kristín       Lauga
113      Kristín       Lauga
114      Kristín       Lauga
115      Kristín      Steina
116      Kristín       Lauga
117      Kristín      Steina
118      Kristín       Lauga
119      Kristín      Steina
120      Kristín      Steina
121      Kristín      Steina
122      Kristín       Lauga
123        Lauga      Steina
124      Kristín       Lauga
125        Lauga      Steina
126      Kristín       Lauga
127        Lauga      Steina
128      Kristín       Lauga
129        Lauga      Steina
130        Lauga      Steina
131        Lauga      Steina
132        Lauga      Steina
133        Lauga      Steina
134        Lauga      Steina
135        Lauga      Steina
136        Lauga      Steina
137     

In [15]:
relationship_df["value"] = 1
relationship_df = relationship_df.groupby(["source","target"], sort=False, as_index=False).sum()

In [20]:
# Create a graph from a pandas dataframe
G = nx.from_pandas_edgelist(relationship_df, 
                            source = "source", 
                            target = "target", 
                            edge_attr = "value", 
                            create_using = nx.Graph())

In [19]:
# %%
from pyvis.network import Network
net = Network(notebook = True, width="1000px", height="700px", bgcolor='#222222', font_color='white')

node_degree = dict(G.degree)

#Setting up node size attribute
nx.set_node_attributes(G, node_degree, 'size')

net.from_nx(G)
net.show("br.html")

br.html


Most important characters in Burial Rites

In [18]:
# Degree centrality
degree_dict = nx.degree_centrality(G)
degree_dict

{'Agnes': 0.8684210526315789,
 'Tóti': 0.7105263157894737,
 'Natan': 0.6578947368421052,
 'Pétur': 0.23684210526315788,
 'Jón': 0.47368421052631576,
 'Margrét': 0.6052631578947368,
 'Steina': 0.3421052631578947,
 'Lauga': 0.3421052631578947,
 'Kristín': 0.2631578947368421,
 'Ingibjörg': 0.21052631578947367,
 'Jóas': 0.23684210526315788,
 'Inga': 0.21052631578947367,
 'Páll': 0.13157894736842105,
 'Róslín': 0.2894736842105263,
 'Fridrik': 0.39473684210526316,
 'Gudmundur': 0.2894736842105263,
 'Björn': 0.21052631578947367,
 'Sigga': 0.42105263157894735,
 'Thorvardur': 0.18421052631578946,
 'Sigrídur': 0.10526315789473684,
 'Haukur': 0.05263157894736842,
 'Gudrún': 0.15789473684210525,
 'Dagga': 0.10526315789473684,
 'Bjarni': 0.18421052631578946,
 'Helga': 0.10526315789473684,
 'Magnús': 0.13157894736842105,
 'Ingveldur': 0.07894736842105263,
 'Kjartan': 0.23684210526315788,
 'Gudbjörg': 0.15789473684210525,
 'Ragnar': 0.05263157894736842,
 'Rósa': 0.23684210526315788,
 'Karitas': 0.210